In [2]:
import os
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import hydrofunctions as hf
from scipy.signal import find_peaks
import time

In [3]:
Direct = "C:/Users/mgalib/Box/Finley_UH_work/Data/"

In [7]:

# function to create a folder to store the results if it does not exist
def ResultsFolder(Folder):
    if os.path.exists(Folder) == False:
        os.makedirs(Folder)

# A function to obtain the peak flow data of a USGS gauge
def read_site_numbers(file_path):
    with open(file_path, 'r') as file:
        # Read the first few lines to determine format
        first_line = file.readline().strip()
        second_line = file.readline().strip()

    try:
        # Attempt to convert to float to check if it's numeric
        float(first_line)
        # If conversion is successful, assume no headers
        skip_lines = 0
    except ValueError:
        # If conversion fails, assume headers are present
        skip_lines = 2

    # Now read the file with appropriate skipping
    site_numbers = np.genfromtxt(file_path, dtype='str', skip_header=skip_lines)
    return site_numbers



def GetFlow(site_no,begin_date,end_date,state):
    # download the discharge data (instantaneous values,15-min) from NWIS

    # Raw data stuff
    Folder1 = Direct + state + '/' + state + '_' + year + '/Raw_Data/Raw_Data_' + site_no + '/'
    ResultsFolder(Folder1)

    # Flood data stuff
    Folder2 = Direct + state + '/' + state + '_' + year + '/Flood_Events/Flood_Events_' + site_no + '/'
    ResultsFolder(Folder2)

    # Check if the Folder1 has any files
    if os.listdir(Folder1):
        print(f"Data already downloaded for {Folder1}. Skipping.")
        return  # Return from the function if data is present

    discharge = hf.NWIS(site_no, 'iv', begin_date, end_date)

    discharge.get_data()


    # save the data as TXT and CSV and store them in the "Raw_Data" folder

    raw_data = pd.DataFrame({'discharge_cfs':discharge.df().iloc[:,0],
                          'qualifiers':discharge.df().iloc[:,1]})
    raw_data.to_csv(Folder1 + "Raw_Discharge_" + site_no + ".txt")
    raw_data.to_csv(Folder1 + "Raw_Discharge_" + site_no + ".csv")


    # generate a discharge hydrograph and save as JPEG, and store them in the "Raw_Data" folder

    flow = pd.DataFrame(raw_data['discharge_cfs'])

    flow.plot(figsize=(12,6))
    plt.title("Discharge Hydrograph of " + site_no)
    plt.legend(["Discharge"], loc='best', edgecolor='k')
    plt.xlabel("Date")
    plt.ylabel("Discharge (cfs)")
    plt.savefig(Folder1 + "Discharge_" + site_no + ".jpeg")
    plt.close()

    # find the peak flow and store separately the data of each flood event

    # set minimal prominence as 40 cfs(the difference between peak and its nearest lowest point)

    peaks,_ = find_peaks(flow['discharge_cfs'], distance=72, prominence=40)

    # separate the flood event(assuming that duration is about 5 days) and save as JPEG and CSV
    # store them in the "Flood_Events" folder

    event_no = 1

    for index in peaks:
    
        if index-200 < 0:
            start = 0
        else:
            start = index-200
        end = index + 200
    
        flood_event=flow[start:end]
    
        flood_event.plot(figsize=(12,6))
        peakvalue = flow[index:index+1]
        plt.scatter(peakvalue.index,peakvalue['discharge_cfs'],color='r')
        plt.title("Flood Event " + str(event_no) +" of "+ site_no)
        plt.legend(["Discharge","Peak Rate"], loc='best',edgecolor='k')
        plt.xlabel("Date")
        plt.ylabel("Discharge (cfs)")
        plt.savefig(Folder2 + "Flood_Event_" + str(event_no) +"_"+ site_no +".jpeg")
        plt.close()

        flood_event.to_csv(Folder2 + "Flood_Event_" + str(event_no) +"_"+ site_no +".csv")

        event_no = event_no + 1

# Define a function to delete empty folders
def delete_empty(path):
    for folder_name in os.listdir(path):
        folder_path = os.path.join(path, folder_name)
        if os.path.isdir(folder_path):
            try:
                os.rmdir(folder_path)
                print(f"* Deleted empty folder: {folder_path}")
            except OSError:
                # The folder is not empty or there is no permission to delete it
                pass



In [9]:

# List of valid state codes
states = ["TN", "AK", "AZ", "AR", "CA", "CO", "CT", "DE", "FL", "GA",
          "HI", "ID", "IL", "IN", "IA", "KS", "KY", "LA", "ME", "MD",
          "MA", "MI", "MN", "MS", "MO", "MT", "NE", "NV", "NH", "NJ",
          "NM", "NY", "NC", "ND", "OH", "OK", "OR", "PA", "RI", "SC",
          "SD", "AL", "TX", "UT", "VT", "VA", "WA", "WV", "WI", "WY"]

gyears = {
    '2000': ['2000', '2001', '2002', '2003', '2004', '2005'],
    '2006': ['2006', '2007', '2008', '2009', '2010'],
    '2011': ['2011', '2012', '2013', '2014', '2015'],
    '2016': ['2016', '2017', '2018', '2019', '2020']
}

# Start timing
start = time.time()

# Loop through each state and each group of years
for state in states:
    for start_year, years in gyears.items():
        for year in years:
            sites_file = Direct + state + '/sites/' + state + '_' + year + '_sites.txt'
           
            
            # Ensure all necessary folders exist
            flood_events_folder = Direct + state + '/' + state + '_' + year + '/Flood_Events'
            raw_data_folder = Direct + state + '/' + state + '_' + year + '/Raw_Data'
            ResultsFolder(flood_events_folder)
            ResultsFolder(raw_data_folder)

            
            # Check if sites file exists to process
            if not os.path.isfile(sites_file):
                print(f"** Sites file missing for {state} {year}. Cannot process.")
                continue
            
            site_no = read_site_numbers(sites_file)
            Results = [None] * len(site_no)
            i = 0
            
            for site in site_no:
                try:
                    intime = time.time()
                    # Placeholder for actual data retrieval function
                    GetFlow(site, year + '-01-01', year + '-12-31', state)
                    delete_empty(flood_events_folder)
                    delete_empty(raw_data_folder)
                    
                except Exception as msg:
                    print(f"** Warnings for {site}: {msg}")
                    Results[i] = 0
                else:
                    Results[i] = 1
                    print(f"({state} {year}) Gauge {site} is done! ({i + 1}/{len(site_no)})")
                    outtime = time.time()
                    elapsed = outtime - intime
                    print(f'Iteration time elapsed is {elapsed:.1f} seconds.')
                i += 1

# End message
end = time.time()
elapsed = (end - start) / 60
mess = 'Finally.' if elapsed < 120 else 'Hope you got some homework done.'
print(f"Discharge data processing is done! Total time elapsed is {elapsed:.1f} minutes. {mess}")


Data already downloaded for C:/Users/mgalib/Box/Finley_UH_work/Data/TN/TN_2000/Raw_Data/Raw_Data_03426385/. Skipping.
(TN 2000) Gauge 03426385 is done! (1/23)
Iteration time elapsed is 0.2 seconds.
Data already downloaded for C:/Users/mgalib/Box/Finley_UH_work/Data/TN/TN_2000/Raw_Data/Raw_Data_03426470/. Skipping.
(TN 2000) Gauge 03426470 is done! (2/23)
Iteration time elapsed is 0.2 seconds.
Data already downloaded for C:/Users/mgalib/Box/Finley_UH_work/Data/TN/TN_2000/Raw_Data/Raw_Data_03430147/. Skipping.
(TN 2000) Gauge 03430147 is done! (3/23)
Iteration time elapsed is 0.2 seconds.
Data already downloaded for C:/Users/mgalib/Box/Finley_UH_work/Data/TN/TN_2000/Raw_Data/Raw_Data_03431300/. Skipping.
(TN 2000) Gauge 03431300 is done! (4/23)
Iteration time elapsed is 0.2 seconds.
Data already downloaded for C:/Users/mgalib/Box/Finley_UH_work/Data/TN/TN_2000/Raw_Data/Raw_Data_03431700/. Skipping.
(TN 2000) Gauge 03431700 is done! (5/23)
Iteration time elapsed is 0.2 seconds.


The NWIS does not have any data for the requested combination of sites, parameters, and dates.


Requested data from https://nwis.waterservices.usgs.gov/nwis/iv/?format=json%2C1.1&sites=03431745&startDT=2000-01-01&endDT=2000-12-31
** Warnings for 03431745: The NWIS does not have any data for the requested combination of sites, parameters, and dates.
Data already downloaded for C:/Users/mgalib/Box/Finley_UH_work/Data/TN/TN_2000/Raw_Data/Raw_Data_034323531/. Skipping.
* Deleted empty folder: C:/Users/mgalib/Box/Finley_UH_work/Data/TN/TN_2000/Flood_Events\Flood_Events_03431745
* Deleted empty folder: C:/Users/mgalib/Box/Finley_UH_work/Data/TN/TN_2000/Raw_Data\Raw_Data_03431745
(TN 2000) Gauge 034323531 is done! (7/23)
Iteration time elapsed is 0.2 seconds.
Data already downloaded for C:/Users/mgalib/Box/Finley_UH_work/Data/TN/TN_2000/Raw_Data/Raw_Data_03432387/. Skipping.
(TN 2000) Gauge 03432387 is done! (8/23)
Iteration time elapsed is 0.2 seconds.
Data already downloaded for C:/Users/mgalib/Box/Finley_UH_work/Data/TN/TN_2000/Raw_Data/Raw_Data_03432390/. Skipping.
(TN 2000) Gauge 0

The NWIS does not have any data for the requested combination of sites, parameters, and dates.


Requested data from https://nwis.waterservices.usgs.gov/nwis/iv/?format=json%2C1.1&sites=03486311&startDT=2000-01-01&endDT=2000-12-31
** Warnings for 03486311: The NWIS does not have any data for the requested combination of sites, parameters, and dates.
Data already downloaded for C:/Users/mgalib/Box/Finley_UH_work/Data/TN/TN_2000/Raw_Data/Raw_Data_03499175/. Skipping.
* Deleted empty folder: C:/Users/mgalib/Box/Finley_UH_work/Data/TN/TN_2000/Flood_Events\Flood_Events_03486311
* Deleted empty folder: C:/Users/mgalib/Box/Finley_UH_work/Data/TN/TN_2000/Flood_Events\Flood_Events_03499175
* Deleted empty folder: C:/Users/mgalib/Box/Finley_UH_work/Data/TN/TN_2000/Raw_Data\Raw_Data_03486311
(TN 2000) Gauge 03499175 is done! (13/23)
Iteration time elapsed is 0.2 seconds.
Data already downloaded for C:/Users/mgalib/Box/Finley_UH_work/Data/TN/TN_2000/Raw_Data/Raw_Data_03536550/. Skipping.
(TN 2000) Gauge 03536550 is done! (14/23)
Iteration time elapsed is 0.2 seconds.
Data already downloaded f

...

Requested data from https://nwis.waterservices.usgs.gov/nwis/iv/?format=json%2C1.1&sites=16237600&startDT=2011-01-01&endDT=2011-12-31


c:\temp\envs\purdue\Lib\site-packages\hydrofunctions\hydrofunctions.py:102: HydroUserWarning: It is not possible to determine the frequency for one of the datasets in this request. This dataset will be set to a frequency of 0 minutes
  warnings.warn(
c:\temp\envs\purdue\Lib\site-packages\hydrofunctions\station.py:317: FutureWarning: It is no longer necessary to call .get_data() to request data.
  warnings.warn(


* Deleted empty folder: C:/Users/mgalib/Box/Finley_UH_work/Data/HI/HI_2011/Flood_Events\Flood_Events_16237600
(HI 2011) Gauge 16237600 is done! (20/68)
Iteration time elapsed is 1.9 seconds.
Requested data from https://nwis.waterservices.usgs.gov/nwis/iv/?format=json%2C1.1&sites=16238000&startDT=2011-01-01&endDT=2011-12-31


c:\temp\envs\purdue\Lib\site-packages\hydrofunctions\station.py:317: FutureWarning: It is no longer necessary to call .get_data() to request data.
  warnings.warn(


KeyboardInterrupt: 